# Лабораторная работа 2.

### Первый набор данных. Цены на золото (14 вариант).
### Второй набор данных. Продажи домов (6 вариант).
### Третий набор данных. Данные о миллионерах (19 вариант).

# Проблемная область 14 варианта.
    - Проблемная область описания относится к финансовой аналитике и прогнозированию цен активов, в частности, к регрессионному анализу цен на золото.
# Проблемная область 6 варианта.
    - Проблемная область в данном случае связана с регрессией в области анализа цен на недвижимость
# Проблемная область 19 варианта.
    - Анализ и прогнозирование богатства, документальное подтверждение и составление рейтингов состоятельных людей.

In [ ]:
import pandas as pd

df_house = pd.read_csv('kc_house_data.csv')

df_house.head()
df_house.info()

# Устранение проблемы пропущенных данных
# Преобразование столбца 'your_column' из float в int
df_house["floors"] = df_house["floors"].astype(int)

# Сохранение измененного DataFrame обратно в CSV
df_house.to_csv("houses.csv", index=False)
# Удаление строк с полностью пустыми значениями
df_cleaned = df_house.dropna(how="all", inplace=True)

In [ ]:
from src.utils import split_stratified_into_train_val_test
import pandas as pd

df_house = pd.read_csv("houses.csv")
display(df_house.floors.value_counts())
display()

data = df_house[["bedrooms", "floors", "condition"]].copy()

df_train, df_val, df_test, y_train, y_val, y_test = (
    split_stratified_into_train_val_test(
        data,
        stratify_colname="floors",
        frac_train=0.60,
        frac_val=0.20,
        frac_test=0.20,
    )
)

display("Обучающая выборка: ", df_train.shape)
display(df_train.floors.value_counts())

display("Контрольная выборка: ", df_val.shape)
display(df_val.floors.value_counts())

display("Тестовая выборка: ", df_test.shape)
display(df_test.floors.value_counts())

In [ ]:
from imblearn.over_sampling import ADASYN

ada = ADASYN()

display("Обучающая выборка: ", df_train.shape)
display(df_train.floors.value_counts())

X_resampled, y_resampled = ada.fit_resample(df_train, df_train["floors"])  # type: ignore
df_train_adasyn = pd.DataFrame(X_resampled)

display("Обучающая выборка после oversampling: ", df_train_adasyn.shape)
display(df_train_adasyn.floors.value_counts())

df_train_adasyn

### Пример бизнес целей для 6 варианта.
    - Ценообразование и прогнозирование цен на недвижимость. Эффект: Упрощение процесса оценки для риэлторов, улучшение точности ценообразования.

    Техническая цель: Построить модель машинного обучения для прогнозирования стоимости недвижимости.
        Вход:

        Количество спален (bedrooms)
        Количество ванных комнат (bathrooms)
        Площадь жилого пространства (sqft_living)
        Площадь участка (sqft_lot)
        Год постройки (yr_built)
        Рейтинг дома (grade)
        Вид, состояние, близость к воде (view, condition, waterfront)
        Почтовый индекс и координаты (zipcode, lat, long)
        Целевой признак:

        Цена недвижимости (price).

    - Идентификация перспективных районов. Эффект: Помощь инвесторам в выборе объектов для вложений.

    Техническая цель: Анализ динамики цен недвижимости по районам для выявления быстро растущих районов.
        Вход:

        Средняя цена домов в почтовом индексе за предыдущие годы.
        Координаты домов (lat, long).
        Число продаж в каждом районе за период.
        Целевой признак:

        Рост средней цены домов в районе.


### 6.Определить проблемы выбранных наборов данных: зашумленность, смещение, актуальность, выбросы, просачивание данных.
#### 1.1. Зашумленность данных
    Возможные ошибки ввода: некорректные значения площади или количества комнат (например, площадь 0, количество комнат слишком велико).
    Сильная корреляция признаков: например, площадь дома и количество комнат могут дублировать информацию.
#### 1.2. Смещение данных
    Набор данных может не охватывать все районы и типы недвижимости, например, роскошные или дешевые дома могут быть представлены неравномерно.
    Временная зависимость: если данные устарели (например, цены из старого периода), это может привести к смещению в прогнозах.
#### 1.3. Актуальность данных
    Если рынок недвижимости изменился (например, после 2020 года из-за пандемии), старые данные могут быть малоактуальны для современных прогнозов.
#### 1.4. Выбросы
    Очень высокие или низкие цены (например, элитная недвижимость или заброшенные дома).
    Аномальные значения площади (например, слишком большие или маленькие площади).
#### 1.5. Просачивание данных (Data Leakage)
    Если в модели используются признаки, которые недоступны на момент прогноза (например, цена или площадь после ремонта), это приведет к завышенной точности модели.

### 7.Привести примеры решения обнаруженных проблем для каждого набора данных.

#### 1.1. Зашумленность данных
        Решение:

        Проверка данных на наличие некорректных значений:
        Исключить записи с площадью 0 или нереалистично большими значениями.
        Проверить диапазон значений для числовых признаков (например, количество комнат не превышает разумных пределов).
        Удаление или сглаживание дублирующихся признаков:
        Если два признака, например, sqft_living и sqft_living15, имеют очень высокую корреляцию, можно исключить один из них.
#### 1.2. Смещение данных
        Решение:

        Применение стратифицированного отбора данных, чтобы обеспечить равномерное покрытие различных типов недвижимости (дешевые, средние, элитные дома).
        Актуализация данных: объединение с дополнительными источниками, которые отражают текущие цены.
#### 1.3. Актуальность данных
        Решение:

        Удаление устаревших записей (например, с датой продажи старше 10 лет).
        Добавление новых данных о ценах и характеристиках недвижимости для текущего рынка.
#### 1.4. Выбросы
        Решение:

        Использование статистических методов (например, межквартильный размах) для выявления выбросов:
        Исключение аномально высоких или низких цен.
        Логическая проверка площадей и количества этажей.
#### 1.5. Просачивание данных
        Решение:

        Исключение признаков, которые невозможно знать в момент прогноза (например, год реновации, если он произошел после продажи).
        Разделение данных на тренировочный и тестовый наборы с учетом временного разрыва.


### 8.Оценить качество каждого набора данных: информативность, степень покрытия, соответствие реальным данным, согласованность меток.

#### 1.1. Информативность
    Положительные стороны:
    Набор включает множество характеристик недвижимости (размеры, состояние, год постройки, координаты), что позволяет решать широкий спектр задач (прогнозирование цены, классификация).
    Ограничения:
    Некоторые признаки, такие как yr_renovated, имеют много нулевых значений, что может снижать информативность.
    Почтовый индекс (zipcode) предоставляет лишь ограниченную информацию о районе.
#### 1.2. Степень покрытия
    Положительные стороны:
    Набор охватывает более 21 000 объектов недвижимости, что достаточно для генерализации моделей.
    Ограничения:
    Данные представлены только для одного региона (вероятно, Сиэтл или его окрестности), что ограничивает применение моделей для других территорий.
#### 1.3. Соответствие реальным данным
    Положительные стороны:
    Данные хорошо описывают основные характеристики недвижимости, которые действительно влияют на цены.
    Ограничения:
    Устаревшие записи (например, дома, проданные более 10 лет назад) могут не отражать текущие рыночные тенденции.
#### 1.4. Согласованность меток
    Положительные стороны:
    Основной целевой признак (price) представлен четко и корректно.
    Ограничения:
    Возможны редкие выбросы или ошибки в данных о цене (например, нереалистично высокая или низкая стоимость).

In [ ]:
import pandas as pd

df = pd.read_csv('Forbes Billionaires.csv')

df.head()
df.info()

# Устранение проблемы пропущенных данных, а именно - замена на const.
df['AgeFillNA'] = df['Age'].fillna(50)

# Разделение столбца Networth на 3 группы
df["Networth_Group"] = pd.qcut(df["Networth"], q=3, labels=[1, 2, 3])
df

In [ ]:
from src.utils import split_stratified_into_train_val_test
import pandas as pd

display(df.Networth_Group.value_counts())
display()

data = df[["Networth_Group", "Networth", "AgeFillNA"]].copy()

df_train, df_val, df_test, y_train, y_val, y_test = (
    split_stratified_into_train_val_test(
        data,
        stratify_colname="Networth_Group",
        frac_train=0.60,
        frac_val=0.20,
        frac_test=0.20,
    )
)

display("Обучающая выборка: ", df_train.shape)
display(df_train.Networth_Group.value_counts())

display("Контрольная выборка: ", df_val.shape)
display(df_val.Networth_Group.value_counts())

display("Тестовая выборка: ", df_test.shape)
display(df_test.Networth_Group.value_counts())

In [ ]:
from imblearn.over_sampling import ADASYN

ada = ADASYN()

display("Обучающая выборка: ", df_train.shape)
display(df_train.Networth_Group.value_counts())

X_resampled, y_resampled = ada.fit_resample(df_train, df_train["Networth_Group"])  # type: ignore
df_train_adasyn = pd.DataFrame(X_resampled)

display("Обучающая выборка после oversampling: ", df_train_adasyn.shape)
display(df_train_adasyn.Networth_Group.value_counts())

df_train_adasyn

В данном примере мы можем видеть достаточную сбалансированность (или же распределение почти равно, метод ADASYN не смог создать новые примеры, как так это не нужно). Это произошло из за дорабатывания исходного файла, так как на стандартном - выполнить данное задание не представляется возможным.

### Пример бизнес цели для 19 варианта
    - Анализ целевой аудитории для элитных товаров и услуг. Эффект: Повышение доходов за счёт фокусировки на платежеспособных клиентах.
    - Определение перспективных индустрий для инвестиций. Эффект: Увеличение доходности инвестиций за счёт выбора наиболее прибыльных секторов.

### 6.Определить проблемы выбранных наборов данных: зашумленность, смещение, актуальность, выбросы, просачивание данных.

Проблемы и их решения:
1. Зашумленность данных
    Проблема: Возможны дублирующиеся или некорректные записи (например, одинаковые имена с разными рангами).
    Решение: Проверить и удалить дубликаты, если они есть.
2. Смещение данных
    Проблема: Набор может быть смещен в сторону представителей более крупных стран или популярных отраслей.
    Решение: Провести анализ распределения по странам и индустриям, а также сбалансировать данные для более равномерного анализа.
3. Актуальность данных
    Проблема: Устаревшие данные могут не отражать текущее состояние богатства.
    Решение: Проверить год публикации данных и, если необходимо, дополнить их более актуальной информацией.
4. Выбросы
    Проблема: Возможны выбросы в данных состояния (например, ошибки ввода).
    Решение: Проверить распределение состояния (например, с помощью диаграммы размаха) и устранить аномалии.
5. Просачивание данных
    Проблема: Если использовать ранги или источники состояния для предсказания состояний, это может привести к неправильной интерпретации.
    Решение: Исключить признаки, которые содержат информацию о целевой переменной.

### 8.Оценить качество каждого набора данных: информативность, степень покрытия, соответствие реальным данным, согласованность меток.

1. Информативность
    Положительные стороны:
    Набор данных предоставляет ключевые параметры: состояние, возраст, страна, индустрия и источник дохода.
    Полезен для анализа распределения богатства по странам, индустриям и возрастным группам.
    Ограничения:
    Возможно, не хватает дополнительных параметров (например, гендер или тренды изменения состояния).
2. Степень покрытия
    Положительные стороны:
    Набор включает информацию о 2600 миллиардерах, что является большим объемом для глобального анализа.
    Ограничения:
    Отсутствие данных о миллиардерах из менее известных стран или отраслей может снижать репрезентативность.
3. Соответствие реальным данным
    Положительные стороны:
    Данные соответствуют информации из открытых источников (Forbes).
    Ограничения:
    Актуальность данных зависит от года публикации (нужно уточнить).
4. Согласованность меток
    Положительные стороны:
    Столбцы (Rank, Networth, Country, Industry) логически согласованы и не содержат явных ошибок.
    Ограничения:
    Возможны дублирующиеся записи или опечатки в текстовых данных (например, в именах или странах).

In [ ]:
import pandas as pd

df = pd.read_csv('FINAL_USO.csv')
df.head()
df.info()

# Устранение проблемы пропущенных данных - медианное значение.
median_value = df['DJ_high'].median()
df['DJ_high'].fillna(median_value, inplace=True)

df


In [10]:
from src.utils import split_stratified_into_train_val_test
import pandas as pd

display(df.PLT_Trend.value_counts())
display()

data = df[["PLT_Trend", "High", "Low"]].copy()

df_train, df_val, df_test, y_train, y_val, y_test = (
    split_stratified_into_train_val_test(
        data,
        stratify_colname="PLT_Trend",
        frac_train=0.60,
        frac_val=0.20,
        frac_test=0.20,
    )
)

display("Обучающая выборка: ", df_train.shape)
display(df_train.PLT_Trend.value_counts())

display("Контрольная выборка: ", df_val.shape)
display(df_val.PLT_Trend.value_counts())

display("Тестовая выборка: ", df_test.shape)
display(df_test.PLT_Trend.value_counts())

PLT_Trend
0    886
1    832
Name: count, dtype: int64

'Обучающая выборка: '

(1030, 3)

PLT_Trend
0    531
1    499
Name: count, dtype: int64

'Контрольная выборка: '

(344, 3)

PLT_Trend
0    177
1    167
Name: count, dtype: int64

'Тестовая выборка: '

(344, 3)

PLT_Trend
0    178
1    166
Name: count, dtype: int64

In [11]:
from imblearn.over_sampling import ADASYN

ada = ADASYN()

display("Обучающая выборка: ", df_train.shape)
display(df_train.PLT_Trend.value_counts())

X_resampled, y_resampled = ada.fit_resample(df_train, df_train["PLT_Trend"])  # type: ignore
df_train_adasyn = pd.DataFrame(X_resampled)

display("Обучающая выборка после oversampling: ", df_train_adasyn.shape)
display(df_train_adasyn.PLT_Trend.value_counts())

df_train_adasyn

'Обучающая выборка: '

(1030, 3)

PLT_Trend
0    531
1    499
Name: count, dtype: int64

'Обучающая выборка после oversampling: '

(1046, 3)

PLT_Trend
0    531
1    515
Name: count, dtype: int64

PLT_Trend        High         Low
0             0  118.459999  118.070000
1             0  114.949997  114.410004
2             0  109.769997  108.940002
3             0  126.120003  125.309998
4             1  122.610001  122.220001
...         ...         ...         ...
1041          1  135.325901  133.909193
1042          1  136.613181  135.565760
1043          1  136.154196  130.907531
1044          1  153.542436  150.981407
1045          1  136.182537  131.184275

[1046 rows x 3 columns]

### Пример бизнес целей для 14 варианта.
    - Оптимизация торговых стратегий. Эффект: Увеличение прибыли трейдеров и инвестиционных фондов.
    - Анализ корреляций между рынками. Эффект: Повышение эффективности диверсификации портфеля и управления рисками.

### 1. Прогнозирование цен на нефть (USO)
Техническая цель: Разработать модель машинного обучения для прогнозирования цены закрытия нефти на следующий день.

Вход:

Цены открытия, максимума, минимума, закрытия нефти за последние N дней (USO_Open, USO_High, USO_Low, USO_Close).
Объем торгов нефтью (USO_Volume).
Финансовые индексы (например, SP_Close, DJ_Close, EU_Trend).
Целевой признак:

Цена закрытия нефти на следующий день (USO_Close).

### 2. Рекомендации для инвесторов
Техническая цель: Разработать систему рекомендаций, которая советует инвесторам, в какие инструменты вкладывать (нефть, акции, индексы).

Вход:

Финансовые показатели (цены открытия, закрытия, объемы торгов для разных инструментов).
Исторические данные о трендах (EU_Trend, USO_Trend).
Предпочтения инвестора (риск, ожидаемая доходность).
Целевой признак:

Вероятность роста выбранного инструмента в ближайшие дни.


### 6.Определить проблемы выбранных наборов данных: зашумленность, смещение, актуальность, выбросы, просачивание данных.

#### 2.1. Зашумленность данных
    Наличие мелких колебаний цен, которые не несут значимой информации для долгосрочного прогноза.
    Пропуски или дублирование данных в датах или финансовых показателях.
#### 2.2. Смещение данных
    Данные могут быть сосредоточены на определенных временных периодах, например, на благоприятных или неблагоприятных для рынка. Это затрудняет генерализацию модели на другие периоды.
    Неполное покрытие всех возможных макроэкономических факторов, влияющих на цены (например, влияние геополитических событий).
#### 2.3. Актуальность данных
    Финансовые рынки изменяются очень быстро. Если данные устарели, модели, обученные на них, не смогут правильно реагировать на текущую динамику.
#### 2.4. Выбросы
    Резкие изменения цен и объемов торгов в периоды нестабильности рынка (например, во время кризисов).
    Аномальные тренды в отдельных финансовых инструментах.
#### 2.5. Просачивание данных (Data Leakage)
    Использование будущих значений (например, цен закрытия следующего дня) при обучении модели.
    Тренды, рассчитанные на основе данных, доступных только после момента прогноза.

### 7.Привести примеры решения обнаруженных проблем для каждого набора данных.

#### 2.1. Зашумленность данных
    Решение:

    Применение методов сглаживания временных рядов:
    Использование скользящих средних или фильтрации данных для устранения мелких колебаний.
    Заполнение пропусков:
    Линейная интерполяция или более сложные методы, такие как KNN, для восстановления недостающих значений.
#### 2.2. Смещение данных
    Решение:

    Добавление данных из других периодов (например, кризисных или стабильных) для лучшей генерализации модели.
    Балансировка данных: включение записей с различными макроэкономическими условиями (например, с изменениями процентных ставок).
#### 2.3. Актуальность данных
    Решение:

    Постоянное обновление данных за счет регулярной выгрузки актуальных финансовых показателей.
    Исключение записей, относящихся к устаревшим периодам, если они не имеют корреляции с текущими тенденциями.
#### 2.4. Выбросы
    Решение:

    Выявление выбросов с помощью методов, таких как Z-оценка или Isolation Forest:
    Аномальные объемы торгов или резкие скачки цен можно сгладить или исключить.
    Анализ контекста выбросов: если выброс вызван реальным событием (например, кризисом), его нужно сохранить.
#### 2.5. Просачивание данных
    Решение:

    Исключение признаков, которые зависят от будущих значений (например, цены закрытия следующего дня).
    Формирование тренировочного и тестового наборов с учетом временной последовательности данных (train-test split на основе дат).

### 8.Оценить качество каждого набора данных: информативность, степень покрытия, соответствие реальным данным, согласованность меток

#### 2.1. Информативность
    Положительные стороны:
    Включает широкий спектр финансовых показателей (цены открытия, закрытия, объемы торгов, тренды).
    Подходит для временного анализа и прогнозирования.
    Ограничения:
    Некоторые трендовые и вспомогательные индикаторы не описаны явно, что затрудняет их интерпретацию.
#### 2.2. Степень покрытия
    Положительные стороны:
    Набор данных включает данные за значительный временной промежуток (1718 записей), что полезно для анализа динамики.
    Ограничения:
    Возможно, набор данных не охватывает все важные макроэкономические факторы (например, данные о процентных ставках, геополитических событиях).
#### 2.3. Соответствие реальным данным
    Положительные стороны:
    Цены и объемы торгов являются стандартными финансовыми метриками и, скорее всего, соответствуют реальным данным.
    Ограничения:
    Актуальность данных может быть ограничена, если набор содержит записи только до определенной даты и не обновляется.
#### 2.4. Согласованность меток
    Положительные стороны:
    Метки, такие как тренды (Trend) и цены (Close), согласованы с соответствующими временными показателями.
    Ограничения:
    Если трендовые данные рассчитываются на основе будущих значений, это может привести к ошибкам в анализе.